## Install Libraries


In [1]:
%pip install "ray[tune]"
# %pip install torch torchvision torchaudio # Uncomment this to install PyTorch 2.0+ on ilab (required version to run this program)

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


## Import Libraries


In [2]:
from collections import OrderedDict
from filelock import FileLock
from ray import tune
from ray.air import session
from ray.air.checkpoint import Checkpoint
from torch.utils.data import random_split
import os
import ray
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import torchvision
import torchvision.transforms as transforms


In [3]:
ray.init(ignore_reinit_error=True, num_cpus=4, num_gpus=4)
print("success")


2023-04-08 02:39:51,112	INFO worker.py:1553 -- Started a local Ray instance.


success


## Data loaders


In [4]:
def load_data(data_dir="./data"):
    transform = transforms.Compose(
        [transforms.ToTensor(), transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))]
    )

    with FileLock(os.path.expanduser("~/.data.lock")):
        trainset = torchvision.datasets.CIFAR10(
            root=data_dir, train=True, download=True, transform=transform
        )

        testset = torchvision.datasets.CIFAR10(
            root=data_dir, train=False, download=True, transform=transform
        )

    return trainset, testset


## Configurable neural network


In [5]:
def flatten(x, start_dim=1, end_dim=-1):
    return x.flatten(start_dim=start_dim, end_dim=end_dim)


In [6]:
# Will need to modify the parameters and the network depending on what you are experimenting with
class Net(nn.Module):
    def __init__(self, kernel_size_1, kernel_size_2):
        super(Net, self).__init__()
        self.conv1 = nn.Conv2d(3, 3, kernel_size_1, padding="same")
        self.conv2 = nn.Conv2d(3, 3, kernel_size_2, padding="same")
        self.fc = nn.Linear(3 * 32 * 32, 10)

    def forward(self, x):
        x = F.relu(self.conv1(x))
        x = F.relu(self.conv2(x))
        x = flatten(x)
        x = self.fc(x)
        return x


## The train function


In [7]:
def train_cifar(config):
    net = Net(
        config["kernel_size_1"], config["kernel_size_2"]
    )  # Will need to modify the parameters depending on what you are experimenting with

    device = "cpu"
    if torch.cuda.is_available():
        device = "cuda:0"
        if torch.cuda.device_count() > 1:
            net = nn.DataParallel(net)
    net.to(device)

    criterion = nn.CrossEntropyLoss()
    optimizer = optim.SGD(net.parameters(), lr=1e-3)

    # Do not modify any code below!
    loaded_checkpoint = session.get_checkpoint()
    if loaded_checkpoint:
        with loaded_checkpoint.as_directory() as loaded_checkpoint_dir:
            model_state, optimizer_state = torch.load(
                os.path.join(loaded_checkpoint_dir, "checkpoint.pt")
            )
            net.load_state_dict(model_state)
            optimizer.load_state_dict(optimizer_state)

    data_dir = os.path.abspath("./data")
    trainset, testset = load_data(data_dir)

    test_abs = int(len(trainset) * 0.8)
    train_subset, val_subset = random_split(
        trainset, [test_abs, len(trainset) - test_abs]
    )

    trainloader = torch.utils.data.DataLoader(
        train_subset, batch_size=64, shuffle=True, num_workers=8
    )
    valloader = torch.utils.data.DataLoader(
        val_subset, batch_size=64, shuffle=True, num_workers=8
    )

    for epoch in range(10):
        running_loss = 0.0
        epoch_steps = 0
        for i, data in enumerate(trainloader, 0):
            inputs, labels = data
            inputs, labels = inputs.to(device), labels.to(device)

            optimizer.zero_grad()

            outputs = net(inputs)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()

            running_loss += loss.item()
            epoch_steps += 1
            if i % 2000 == 1999:
                print(
                    f"[{epoch + 1}, {i + 1:>5} loss: {running_loss / epoch_steps:.3f}]"
                )
                running_loss = 0.0

        val_loss = 0.0
        val_steps = 0
        total = 0
        correct = 0
        for i, data in enumerate(valloader, 0):
            with torch.no_grad():
                inputs, labels = data
                inputs, labels = inputs.to(device), labels.to(device)

                outputs = net(inputs)
                _, predicted = torch.max(outputs.data, 1)
                total += labels.size(0)
                correct += (predicted == labels).sum().item()

                loss = criterion(outputs, labels)
                val_loss += loss.cpu().numpy()
                val_steps += 1

        os.makedirs("my_model", exist_ok=True)
        torch.save((net.state_dict(), optimizer.state_dict()), "my_model/checkpoint.pt")
        checkpoint = Checkpoint.from_directory("my_model")
        session.report(
            {"loss": (val_loss / val_steps), "accuracy": correct / total},
            checkpoint=checkpoint,
        )
    print("Finished Training")


## Test set accuracy


In [8]:
def test_best_model(best_result):
    best_trained_model = Net(
        best_result.config["kernel_size_1"], best_result.config["kernel_size_2"]
    )  # Will need to modify the parameters depending on what you are experimenting with

    # Do not modify any code below!
    device = "cuda:0" if torch.cuda.is_available() else "cpu"
    best_trained_model.to(device)

    checkpoint_path = os.path.join(
        best_result.checkpoint.to_directory(), "checkpoint.pt"
    )

    model_state, optimizer_state = torch.load(checkpoint_path)

    new_model_state = OrderedDict()
    for key, value in model_state.items():
        name = key[7:]  # remove `module.`
        new_model_state[name] = value

    best_trained_model.load_state_dict(new_model_state)

    trainset, testset = load_data()

    testloader = torch.utils.data.DataLoader(
        testset, batch_size=4, shuffle=False, num_workers=2
    )

    correct = 0
    total = 0
    with torch.no_grad():
        for data in testloader:
            images, labels = data
            images, labels = images.to(device), labels.to(device)
            outputs = best_trained_model(images)
            _, predicted = torch.max(outputs.data, 1)
            total += labels.size(0)
            correct += (predicted == labels).sum().item()

    print(f"Best trial test set accuracy: {correct / total}")


## Configuring the search space


In [9]:
# You will be experimenting with the hyperparameters here
# Use tune.grid_search to specify what values you want to experiment with a hyperparameter
config = {
    "kernel_size_1": tune.grid_search([1, 2, 3, 5, 10, 15, 32]),
    "kernel_size_2": tune.grid_search([1, 2, 3, 5, 10, 15, 32]),
}


In [10]:
# Do not modify any code below!
def main(config):
    tuner = tune.Tuner(
        tune.with_resources(
            tune.with_parameters(train_cifar),
            resources={"cpu": 4, "gpu": 4},
        ),
        param_space=config,
    )
    results = tuner.fit()

    best_result = results.get_best_result("accuracy", "max")

    print(f"Best trial config: {best_result.config}")
    print(f"Best trial final validation loss: {best_result.metrics['loss']}")
    print(f"Best trial final validation accuracy: {best_result.metrics['accuracy']}")

    test_best_model(best_result)

    return results.get_dataframe("accuracy", "max")


results_df = main(config)


0it [00:00, ?it/s]far pid=2659049) 
  0%|          | 0/170498071 [00:00<?, ?it/s]


(train_cifar pid=2659049) Downloading https://www.cs.toronto.edu/~kriz/cifar-10-python.tar.gz to /common/home/vig4/ray_results/train_cifar_2023-04-08_02-39-52/train_cifar_2a8b9_00000_0_kernel_size_1=1,kernel_size_2=1_2023-04-08_02-39-52/data/cifar-10-python.tar.gz


100%|█████████▉| 170311680/170498071 [00:02<00:00, 78723545.01it/s]


(train_cifar pid=2659049) Files already downloaded and verified


(train_cifar pid=2659049) /koko/system/anaconda/envs/python39/lib/python3.9/site-packages/torchvision/transforms/functional.py:79: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
(train_cifar pid=2659049)   img = torch.ByteTensor(torch.ByteStorage.from_buffer(pic.tobytes()))
(train_cifar pid=2659049) /koko/system/anaconda/envs/python39/lib/python3.9/site-packages/torchvision/transforms/functional.py:79: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
(train_cifar pid=2659049)   img = torch.ByteTensor(torch.ByteStorage.fr

...

(train_cifar pid=2659049) Finished Training


2023-04-08 04:04:14,233	INFO tune.py:798 -- Total run time: 5062.07 seconds (5061.68 seconds for the tuning loop).


Best trial config: {'kernel_size_1': 32, 'kernel_size_2': 15}
Best trial final validation loss: 1.5852713106544154
Best trial final validation accuracy: 0.4401
Files already downloaded and verified
Files already downloaded and verified


/koko/system/anaconda/envs/python39/lib/python3.9/site-packages/torchvision/transforms/functional.py:79: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  img = torch.ByteTensor(torch.ByteStorage.from_buffer(pic.tobytes()))
/koko/system/anaconda/envs/python39/lib/python3.9/site-packages/torchvision/transforms/functional.py:79: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  img = torch.ByteTensor(torch.ByteStorage.from_buffer(pic.tobytes()))
/common/home/vig4/.local/lib/python3.9/site-packages/torch/nn/modules/conv.py:

Best trial test set accuracy: 0.4436


In [11]:
results_df.drop(
    columns=[
        "should_checkpoint",
        "timesteps_total",
        "episodes_total",
        "training_iteration",
        "trial_id",
        "experiment_id",
        "date",
        "timestamp",
        "pid",
        "hostname",
        "node_ip",
        "time_since_restore",
        "timesteps_since_restore",
        "iterations_since_restore",
        "warmup_time",
        "logdir",
    ]
)


loss  accuracy  time_this_iter_s   done  time_total_s   
0   2.037902    0.2896          8.301019  False     99.845481  \
1   1.987400    0.3061          9.138083  False     96.590099   
2   2.037943    0.2758          8.932103  False    106.843102   
3   1.819601    0.3722          8.308395  False     97.656941   
4   1.762772    0.3752          8.553326  False    117.028346   
5   1.790939    0.3631          9.103287  False     97.248402   
6   1.789791    0.3668          8.422707  False     93.929627   
7   2.090870    0.2644          8.155567  False     89.809458   
8   1.917459    0.3376          8.314139  False     89.357210   
9   2.290692    0.1476          8.185039  False    111.252181   
10  1.928808    0.3333          8.166508  False    109.321914   
11  1.808778    0.3549          8.469549  False     89.472510   
12  1.742792    0.3823          8.156816  False     88.398415   
13  1.666191    0.4136          8.234896  False     91.077245   
14  1.960440    0.3175          8.235396  False     89.452975   
15  1.784544    0.3816          8.709921  False    108.987883   
16  1.824338    0.3591          8.434139  False    107.149391   
17  1.906465    0.3323          8.142096  False     89.390233   
18  1.714530    0.3976          9.097321  False     97.276451   
19  1.748798    0.3878          9.138460  False     99.535221   
20  1.644069    0.4197          9.092000  False     98.671364   
21  1.778055    0.3847          9.072345  False    115.670769   
22  2.027644    0.3107          9.113224  False    117.498786   
23  1.816703    0.3626          9.179218  False     97.117819   
24  1.770813    0.3846          9.003188  False    104.643205   
25  1.740037    0.3801          8.691769  False     96.053167   
26  1.685711    0.4048          8.882262  False     96.106746   
27  1.663852    0.4138          9.181546  False    119.141425   
28  1.726724    0.4058          8.981223  False    119.635933   
29  1.786230    0.3753          9.053860  False     97.496894   
30  1.748109    0.3845          8.950305  False     96.482765   
31  1.741949    0.4008          8.938252  False     96.682004   
32  1.712792    0.3914          9.136689  False     96.416933   
33  1.596973    0.4297          8.982767  False    115.535136   
34  1.560285    0.4338          9.128261  False    117.156399   
35  1.888824    0.3360          8.692824  False     95.563684   
36  1.731673    0.3816          8.954299  False     95.584831   
37  1.771370    0.3766          8.924781  False     95.112547   
38  1.675261    0.3989          9.012243  False    114.944851   
39  1.607104    0.4324          8.958344  False    112.117193   
40  1.637841    0.4165          8.668678  False     96.051652   
41  1.585271    0.4401          8.941783  False     98.082004   
42  1.935695    0.3040          9.276339  False    101.445055   
43  1.688339    0.4066          9.640108  False    102.542678   
44  1.676869    0.4183          9.799485  False    120.616856   
45  1.660574    0.4104          9.639954  False    121.076788   
46  1.586749    0.4341          9.567955  False    109.517335   
47  1.614628    0.4283          9.662141  False    102.977032   
48  1.571906    0.4422          9.905318  False     96.425159   

    config/kernel_size_1  config/kernel_size_2  
0                      1                     1  
1                      2                     1  
2                      3                     1  
3                      5                     1  
4                     10                     1  
5                     15                     1  
6                     32                     1  
7                      1                     2  
8                      2                     2  
9                      3                     2  
10                     5                     2  
11                    10                     2  
12                    15                     2  
13                    32                     2  
14                    